In [27]:
# %% allow reloading of modules
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


#### Note: ensure the you are in the `notebooks` directory when using the `jupyter notebook` command 

In [28]:
import os
path_parent = os.path.dirname(os.getcwd())
os.getcwd()

'/home/joemcormier/pycrash/projects/validation - single vehicle motion'

In [29]:
import sys
#sys.path.append("/home/jmc/Documents/pycrash")
sys.path.append("/home/joemcormier/pycrash/")

In [30]:
import pycrash
from pycrash.project import Project, project_info, load_project
from pycrash.vehicle import Vehicle
from pycrash.kinematics import SingleMotion

In [31]:
os.getcwd()

'/home/joemcormier/pycrash/projects/validation - single vehicle motion'

In [32]:
import pandas as pd
import numpy as np
import math
import plotly.io as pio
pio.renderers.default = "firefox"
from scipy import integrate
pd.options.display.max_columns = None
pd.options.display.max_rows = None
from IPython import get_ipython
from IPython.display import display
get_ipython().run_line_magic('matplotlib', 'qt')

### Load Project Datafile that was created when project was instantiated
- the project object contains information needed to run other parts of Pycrash

#### Get project information - used to import project object

In [33]:
project_info('validation - single vehicle motion')

This saved project contains:
Object of type "project" with name "validation - single vehicle motion"
list objects in this order for loading project: ['validation - single vehicle motion']
Example: project_name, veh1, veh2 = load_project('project_name')


#### Load project and print contents

In [34]:
proj = load_project('validation - single vehicle motion')
proj.show()

----------------------------------  ------------------------  -----------  ---------------  --------------------
Project                             Description               Impact Type  Simulation Type  Note
validation - single vehicle motion  planar motion simulation               SV               pc crash comparisons
----------------------------------  ------------------------  -----------  ---------------  --------------------


In [35]:
proj.__dict__

{'name': 'validation - single vehicle motion',
 'project_path': '/home/jmc/Documents/pycrash/projects/',
 'pdesc': 'planar motion simulation',
 'sim_type': 'SV',
 'impact_type': None,
 'note': 'pc crash comparisons',
 'type': 'project'}

### Generate dataframe with driver inputs
- use validation steer / brake / throttle inputs
- inputs are same dt as pycrash will have to check in future

In [36]:
pc_crash_column_names = ['t', 'ax', 'ay', 'az', 'phi_deg', 'rf_fy', 'lf_fy',
                         'rr_fy', 'lr_fy', 'delta_deg', 'rf_delta_deg', 'steer', 
                         'steer_rate', 'X', 'Y', 'Z', 'roll', 'pitch', 'theta_deg',
                         'Vx', 'Vy', 'Vz']

In [45]:
df = pd.read_excel(os.path.join(path_parent, 'data', 'external', '15-mph-steer-data.xlsx'),
                            na_filter = False, header = None, names = pc_crash_column_names, skiprows = 1)

FileNotFoundError: [Errno 2] No such file or directory: '/home/joemcormier/pycrash/projects/data/external/15-mph-steer-data.xlsx'

In [38]:
# convert velocities to fps
df.Vx = [x * 1.46667 for x in df.Vx]
df.Vy = [x * 1.46667 for x in df.Vy]
df.Vz = [x * 1.46667 for x in df.Vz]

# convert acceleration to fps/s
df.ax = [x * 32.2 for x in df.ax]
df.ay = [x * 32.2 for x in df.ay]
df.az = [x * 32.2 for x in df.az]

# convert tire forces to lb
df.lf_fy = [x * 1000 for x in df.lf_fy]
df.rf_fy = [x * 1000 for x in df.rf_fy]
df.lr_fy = [x * 1000 for x in df.lr_fy]
df.rr_fy = [x * 1000 for x in df.rr_fy]

# steer angle in radians
df['delta_rad'] = [x / 180 * math.pi for x in df.delta_deg]

In [39]:
# integrate velocities to get displacements
df['Dx'] = 0 + integrate.cumtrapz(list(df.Vx), list(df.t), initial=0)
df['Dy'] = 0 + integrate.cumtrapz(list(df.Vy), list(df.t), initial=0)
df.head()

t   ax   ay   az  phi_deg  rf_fy  lf_fy  rr_fy  lr_fy  delta_deg  \
0  0.0  0.0  0.0  0.0      0.0    0.0    0.0    0.0    0.0        0.0   
1  0.1  0.0  0.0  0.0      0.0    0.0    0.0    0.0    0.0        0.0   
2  0.2  0.0  0.0  0.0      0.0    0.0    0.0    0.0    0.0        0.0   
3  0.3  0.0  0.0  0.0      0.0    0.0    0.0    0.0    0.0        0.0   
4  0.4  0.0  0.0  0.0      0.0    0.0    0.0    0.0    0.0        0.0   

   rf_delta_deg  steer  steer_rate    X    Y     Z  roll  pitch  theta_deg  \
0           0.0    0.0           0  0.0  0.0  1.79   0.0    0.0        0.0   
1           0.0    0.0           0  2.2  0.0  1.79   0.0    0.0        0.0   
2           0.0    0.0           0  4.4  0.0  1.79   0.0    0.0        0.0   
3           0.0    0.0           0  6.6  0.0  1.79   0.0    0.0        0.0   
4           0.0    0.0           0  8.8  0.0  1.79   0.0    0.0        0.0   

          Vx   Vy   Vz  delta_rad         Dx   Dy  
0  32.266813  0.0  0.0        0.0   0.000000  0.0  
1  32.266813  0.0  0.0        0.0   3.226681  0.0  
2  32.266813  0.0  0.0        0.0   6.453363  0.0  
3  32.266813  0.0  0.0        0.0   9.680044  0.0  
4  32.266813  0.0  0.0        0.0  12.906725  0.0

### Load Validation Data

In [40]:
# validation vehicle data

vehicle_input_dict = {"year":2004,
"make":"Chevrolet",
"model":"Malibu",
"weight":3298,
"vin":"1G1ZU54854F135916",
"brake":0,
"steer_ratio":15.9,
"init_x_pos":0,
"init_y_pos":0,
"head_angle":0,
"width":70 / 12,
"length":187 / 12,
"hcg":21.5 / 12,
"lcgf":38.1 / 12,
"lcgr":67.9 / 12,
"wb":106 / 12,
"track":60 / 12,
"f_hang":38 / 12,
"r_hang":43 / 12,
"tire_d":26.2 / 12,
"tire_w":8.5 / 12,
"izz":2040,
"fwd":1,
"rwd":0,
"awd":0,
"A":100,
"B":41,
"k":1000,
"L":0,
"c":0,
"vx_initial":0,
"vy_initial":0,
"omega_z":0}

In [41]:
end_time = df.t.max()  
t = np.arange(0, end_time + 0.1, 0.1).tolist()
throttle = [0] * len(t)                      
brake = [0] * len(t)                         
steer = list(df.steer)                                   
driver_input_dict = {'t':t, 'throttle':throttle, 'brake':brake, 'steer':steer}
driver_input_df = pd.DataFrame.from_dict(driver_input_dict)
print('Vehicle Driver Inputs:')
driver_input_df.head()

Vehicle Driver Inputs:


t  throttle  brake  steer
0  0.0         0      0    0.0
1  0.1         0      0    0.0
2  0.2         0      0    0.0
3  0.3         0      0    0.0
4  0.4         0      0    0.0

In [42]:
driver_input_df.t.iloc[-1]

10.9

### Assign validation data to veh2

In [43]:
veh2 = Vehicle('Veh2', vehicle_input_dict)
veh2.driver_input = driver_input_df
# apply validation data as a model result
veh2.model = df

Vehicle inputs for Veh2 applied succesfully


### Create Pycrash vehicle:
- "Vehicle" stores information about a single vehicle - all possible inputs do not need to be entered
- creating a Vehicle requries a "name" which is used to identify the vehicle in outputs / plots etc. 

In [44]:
veh1 = Vehicle('Veh1', vehicle_input_dict)
#veh1.driver_input = driver_input_df
t = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]
brake = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
throttle = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
steer = [0, 0, -360, -360, -360, -360, -360, -360, -360, -360, -360, -360]
veh1.time_inputs(t, throttle, brake, steer)
veh1.vx_initial = 35
veh1.hcg = 0.5   # vary cg height

Vehicle inputs for Veh1 applied succesfully
Driver inputs applied to Veh1


/home/joemcormier/env/lib/python3.7/site-packages/pandas/core/reshape/merge.py:1097: UserWarning:

You are merging on int and float columns where the float values are not equal to their int representation



Error: could not locate runnable browser

### Create Single Motion Instance
- simulation is run when instance is created

In [46]:
run = SingleMotion('15_mph_steer', veh1)

Maximum allowable friction: 0.76
Time step for vehicle motion (s) : 0.01
Maximum tire slip angle (deg): 10.00
Driver input for Veh1 of shape = (1101, 4)
Vehicle motion will be simulated for 11.0 seconds


### View Driver Inputs

### Plot Motion

In [20]:
run.plot_model()

In [47]:
#run.veh.model.plot(x = 't', y = 'ay')

### Plot Vehicle Motion

In [28]:
len(run.veh.model)

1091

In [47]:
i = 1090
print(f"Time: {run.veh.model.t[i]}")
run.global_motion(i)

Time: 10.9
 dx > dy -> adj_x = 1.184415029350034, adj_y = 1
dx_min = -18.0, dx_max = 196.0
dy_min = -105.10924590600452, dy_max = 15.0


### Compare to PC Crash Model

In [23]:
from pycrash.visualization.kinematics_compare import compare_kinematics

In [24]:
# calculate vehicle slip angle for pycrash model - need to add
phi_rad = []
phi_deg = []
for i in range(len(run.veh.model.t)):
    phi_rad.append(math.atan2(run.veh.model.vy[i], run.veh.model.vx[i]) * - 1) 
    phi_deg.append(math.atan2(run.veh.model.vy[i], run.veh.model.vx[i]) * -1 *(180 / math.pi))
    
run.veh.model['phi_rad'] = phi_rad
run.veh.model['phi_deg'] = phi_deg

In [25]:
compare_kinematics(run.veh.model, df, 'pycrash', 'validate')

In [48]:
from pycrash.visualization.tire_details import tire_details, vertical_forces

In [49]:
tire_details(run.veh)

In [68]:
run.veh.model.iloc[200,:]

t                2.000000
vx              20.509839
vy              -2.473148
Vx              18.531539
Vy              -9.047801
Vr              20.622334
oz_deg         -44.585357
oz_rad          -0.778161
delta_deg      -22.415100
delta_rad       -0.391217
turn_rX         11.627154
turn_rY        -23.814522
turn_rR         26.501362
au              -5.866065
av             -18.116266
ax              -3.980454
ay              -2.298734
ar               4.596541
Ax             -11.596872
Ay             -15.103720
Ar              19.042316
alphaz          -0.836052
alphaz_deg     -47.902276
beta_deg       -26.023387
beta_rad        -0.454194
lf_fx         -168.011112
lf_fy         -407.320794
rf_fx         -432.805063
rf_fy        -1049.278824
rr_fx           -0.000000
rr_fy         -329.856099
lr_fx           -0.000000
lr_fy          -69.054994
lf_alpha        -0.134283
rf_alpha        -0.176817
rr_alpha        -0.084593
lr_alpha        -0.101962
lf_lock          0.000000
rf_lock     

In [69]:
vertical_forces(run.veh)

### Get position data for validation vehicle

In [32]:
from pycrash.visualization.cg_motion_compare import cg_motion

In [33]:
cg_motion(run.veh.model, df, 'pycrash', 'validate')

 dx > dy -> adj_x = 1.5160365477816333, adj_y = 1
dx_min = 0.0, dx_max = 83.0
dy_min = -45.35665057609248, dy_max = 1.1296546230300288
